## Determine metrics for timestamped trajectory evaluation

For trajectory information, we have spatial ground truth but **no** temporal ground truth. This is not surprising since the time taken to travel the same route on different days can be different based on the traffic conditions, train delays, etc. We capture high quality (high accuracy/high frequency/always on) temporal data from two different phone during the travel, and mark the temporal ground truth for the start and end of travel segments (trip/section) on the phone.

In this notebook, we explore the various options to create a _reference_ trajectory using the spatial ground truth and the timestamped accuracy control trajectories from android and iOS. We can then use the reference trajectory to evaluate the spatio-temporal accuracy of the experiment trajectories.

#### Import all required modules

In [1]:
# for reading and validating data
import emeval.input.spec_details as eisd
import emeval.input.phone_view as eipv
import emeval.input.eval_view as eiev

In [2]:
# Visualization helpers
import emeval.viz.phone_view as ezpv
import emeval.viz.eval_view as ezev
import emeval.viz.geojson as ezgj
import pandas as pd

In [3]:
import emeval.metrics.reference_trajectory as emr
import emeval.metrics.DTW as dtw

/Users/kinjal/miniconda-23.1.0/envs/emissioneval/lib/python3.11/site-packages/pyproj/crs/crs.py:143: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
/Users/kinjal/miniconda-23.1.0/envs/emissioneval/lib/python3.11/site-packages/pyproj/crs/crs.py:143: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)


In [4]:
# For computation
import numpy as np
import math
import functools
import scipy.stats as stats
import matplotlib.pyplot as plt

In [5]:
import geopandas as gpd
import shapely as shp
import arrow

In [6]:
import folium
import branca.element as bre
import geojson as gj
import copy

In [7]:
import anytree as at
import anytree.importer as ati

#### Load all data

In [8]:
DATASTORE_LOC = "bin/data/"
AUTHOR_EMAIL = "shankari@eecs.berkeley.edu"
sd_la = eisd.FileSpecDetails(DATASTORE_LOC, AUTHOR_EMAIL, "unimodal_trip_car_bike_mtv_la")
sd_sj = eisd.FileSpecDetails(DATASTORE_LOC, AUTHOR_EMAIL, "car_scooter_brex_san_jose")
sd_ucb = eisd.FileSpecDetails(DATASTORE_LOC, AUTHOR_EMAIL, "train_bus_ebike_mtv_ucb")

After iterating over 1 entries, entry found
Found spec = Round trip car and bike trip in the South Bay
Evaluation ran from 2019-07-20T00:00:00-07:00 -> 2020-04-29T17:00:00-07:00
After iterating over 1 entries, entry found
Found spec = Multi-modal car scooter BREX trip to San Jose
Evaluation ran from 2019-07-20T00:00:00-07:00 -> 2020-04-29T17:00:00-07:00
After iterating over 1 entries, entry found
Found spec = Multimodal multi-train, multi-bus, ebike trip to UC Berkeley
Evaluation ran from 2019-07-16T00:00:00-07:00 -> 2020-04-30T00:00:00-07:00


In [9]:
import importlib
importlib.reload(emr)

<module 'emeval.metrics.reference_trajectory' from '/Users/kinjal/Code/openpath/mobilitynet-analysis-scripts/emeval/metrics/reference_trajectory.py'>

In [10]:
pv_la = eipv.PhoneView(sd_la)

-------------------- About to read transitions from server --------------------
Reading data for android phones
Loading transitions for phone ucb-sdb-android-1
Loading transitions for phone ucb-sdb-android-2
Loading transitions for phone ucb-sdb-android-3
Loading transitions for phone ucb-sdb-android-4
Reading data for ios phones
Loading transitions for phone ucb-sdb-ios-1
Loading transitions for phone ucb-sdb-ios-2
Loading transitions for phone ucb-sdb-ios-3
Loading transitions for phone ucb-sdb-ios-4
-------------------- About to fill calibration ranges --------------------
Processing data for android phones
Processing transitions for phone ucb-sdb-android-1
Filtered 86 total -> 0 calibration transitions 
Processing transitions for phone ucb-sdb-android-2
Filtered 86 total -> 0 calibration transitions 
Processing transitions for phone ucb-sdb-android-3
Filtered 86 total -> 0 calibration transitions 
Processing transitions for phone ucb-sdb-android-4
Filtered 86 total -> 0 calibration

In [11]:
pv_sj = eipv.PhoneView(sd_sj)

-------------------- About to read transitions from server --------------------
Reading data for android phones
Loading transitions for phone ucb-sdb-android-1
Loading transitions for phone ucb-sdb-android-2
Loading transitions for phone ucb-sdb-android-3
Loading transitions for phone ucb-sdb-android-4
Reading data for ios phones
Loading transitions for phone ucb-sdb-ios-1
Loading transitions for phone ucb-sdb-ios-2
Loading transitions for phone ucb-sdb-ios-3
Loading transitions for phone ucb-sdb-ios-4
-------------------- About to fill calibration ranges --------------------
Processing data for android phones
Processing transitions for phone ucb-sdb-android-1
Filtered 86 total -> 0 calibration transitions 
Processing transitions for phone ucb-sdb-android-2
Filtered 86 total -> 0 calibration transitions 
Processing transitions for phone ucb-sdb-android-3
Filtered 86 total -> 0 calibration transitions 
Processing transitions for phone ucb-sdb-android-4
Filtered 86 total -> 0 calibration

In [12]:
pv_ucb = eipv.PhoneView(sd_ucb)

-------------------- About to read transitions from server --------------------
Reading data for android phones
Loading transitions for phone ucb-sdb-android-1
Loading transitions for phone ucb-sdb-android-2
Loading transitions for phone ucb-sdb-android-3
Loading transitions for phone ucb-sdb-android-4
Reading data for ios phones
Loading transitions for phone ucb-sdb-ios-1
Loading transitions for phone ucb-sdb-ios-2
Loading transitions for phone ucb-sdb-ios-3
Loading transitions for phone ucb-sdb-ios-4
-------------------- About to fill calibration ranges --------------------
Processing data for android phones
Processing transitions for phone ucb-sdb-android-1
Filtered 102 total -> 0 calibration transitions 
Processing transitions for phone ucb-sdb-android-2
Filtered 90 total -> 0 calibration transitions 
Processing transitions for phone ucb-sdb-android-3
Filtered 90 total -> 0 calibration transitions 
Processing transitions for phone ucb-sdb-android-4
Filtered 90 total -> 0 calibratio

### Test trajectories

We select four different runs as our deep-dive dataset to explore various reference trajectory creation options. These are:
1. `easiest`: overground, unimodal trip by car and bike where both control phones had very little error
1. `weird_android`: different run of trip (1) where the android control phone had very poor quality data even though we requested high quality data
1. `temporal_zigzags`: this trip is really the motivation for spatio-temporal accuracy. It is an underground trip with zig zags a prior point along the trip, classic example of why spatio-temporal accuracy is needed
1. `backtracking`: trip that includes a short u-turn + backtrack to ensure that real zigzags are respected

In [13]:
subway_underground_section = pv_ucb.map()["android"]["ucb-sdb-android-3"]["evaluation_ranges"][0]["evaluation_trip_ranges"][0]["evaluation_section_ranges"][5]

deep_dive_dataset = {
    "easiest": {
        "ground_truth": {
            "leg": sd_la.get_ground_truth_for_leg("suburb_city_driving_weekend", "suburb_city_driving_weekend", sd_la.eval_start_ts, sd_la.eval_end_ts)
        },
        "temporal_control": {
            "android": pv_la.map()["android"]["ucb-sdb-android-1"]["evaluation_ranges"][1]["evaluation_trip_ranges"][0],
            "ios": pv_la.map()["ios"]["ucb-sdb-ios-1"]["evaluation_ranges"][1]["evaluation_trip_ranges"][0]
        }
    },
    "weird_android": {
        "ground_truth": {
            "leg": sd_la.get_ground_truth_for_leg("suburb_city_driving_weekend", "suburb_city_driving_weekend", sd_la.eval_start_ts, sd_la.eval_end_ts)
        },
        "temporal_control": {
            "android": pv_la.map()["android"]["ucb-sdb-android-1"]["evaluation_ranges"][0]["evaluation_trip_ranges"][0],
            "ios": pv_la.map()["ios"]["ucb-sdb-ios-1"]["evaluation_ranges"][0]["evaluation_trip_ranges"][0]
        }
    },
    "temporal_zigzags": {
        "ground_truth": {
            "leg": sd_ucb.get_ground_truth_for_leg("mtv_to_berkeley_sf_bart", "subway_underground", subway_underground_section["start_ts"], subway_underground_section["end_ts"])
        },
        "temporal_control": {
            "android": pv_ucb.map()["android"]["ucb-sdb-android-1"]["evaluation_ranges"][0]["evaluation_trip_ranges"][0]["evaluation_section_ranges"][5],
            "ios": pv_ucb.map()["ios"]["ucb-sdb-ios-1"]["evaluation_ranges"][0]["evaluation_trip_ranges"][0]["evaluation_section_ranges"][5]
        }
    },
    "backtracking": {
        "ground_truth": {
            "leg": sd_sj.get_ground_truth_for_leg("bus trip with e-scooter access", "city_escooter", sd_ucb.eval_start_ts, sd_ucb.eval_end_ts)            
        },
        "temporal_control": {
            "android": pv_sj.map()["android"]["ucb-sdb-android-1"]["evaluation_ranges"][0]["evaluation_trip_ranges"][1]["evaluation_section_ranges"][1],
            "ios": pv_sj.map()["ios"]["ucb-sdb-ios-1"]["evaluation_ranges"][0]["evaluation_trip_ranges"][1]["evaluation_section_ranges"][1]
        }
    }
}

In [14]:
def add_section_and_points(curr_map, eval_section, loc_df_label, layer_name, disp_color, with_points=False):
    sensed_location_df = eval_section[loc_df_label]
    print("Adding section for %s with length %s" % (layer_name, len(sensed_location_df)))
    sensed_section_gj = gj.Feature(geometry=gj.LineString(coordinates=list(zip(sensed_location_df.longitude, sensed_location_df.latitude))),
                                   properties={"style": {"color": disp_color}, "ts": list(sensed_location_df.ts)})
    sensed_leg_gj_feature = folium.GeoJson(sensed_section_gj, name="sensed_values (%s)" % layer_name)
    curr_map.add_child(sensed_leg_gj_feature)
    if with_points:
        sensed_leg_gj_points = ezgj.get_point_markers(sensed_section_gj, name="sensed_points (%s)" % layer_name,
                                                      color=disp_color, tz="America/Los_Angeles")
        curr_map.add_child(sensed_leg_gj_points)

def display_gt_and_controls(entry, loc_df_label, with_points=False):
    curr_map = folium.Map()
    print("Using ground truth %s" % entry["ground_truth"]["leg"]["id"])
    gt_leg_gj = eisd.SpecDetails.get_geojson_for_leg(entry["ground_truth"]["leg"])
    gt_leg_gj_feature = folium.GeoJson(gt_leg_gj, name="ground_truth")
    curr_map.add_child(gt_leg_gj_feature)
    if with_points:
        gt_leg_gj_points = ezgj.get_point_markers(gt_leg_gj[2], name="ground_truth_points", color="green")
        curr_map.add_child(gt_leg_gj_points)
    
    add_section_and_points(curr_map, entry["temporal_control"]["android"], loc_df_label, "android", "orange", with_points)
    add_section_and_points(curr_map, entry["temporal_control"]["ios"], loc_df_label, "ios", "purple", with_points)
    
    curr_map.fit_bounds(gt_leg_gj_feature.get_bounds())
    folium.LayerControl().add_to(curr_map)
    return curr_map

In [15]:
map_list = [display_gt_and_controls(e, "location_df") for e in deep_dive_dataset.values()]; len(map_list)

Using ground truth suburb_city_driving_weekend
Adding section for android with length 809
Adding section for ios with length 667
Using ground truth suburb_city_driving_weekend
Adding section for android with length 467
Adding section for ios with length 718
Using ground truth subway_underground
Adding section for android with length 749
Adding section for ios with length 404
Using ground truth city_escooter
Adding section for android with length 1207
Adding section for ios with length 1016


4

In [16]:
evaluation_maps = bre.Figure()
for i, curr_map in enumerate(map_list):
    evaluation_maps.add_subplot(2, 2, i+1).add_child(curr_map)
evaluation_maps

Features of interest in the maps:
- `easiest`: android and ios match beautifully with ground truth
- `weird_android`: ios matches with ground truth, but android (orange) has inconsistencies near the start (triangle) and deviates a couple of other times in the middle
- `temporal_zigzags`: the ios data is much less accurate, with loops around San Bruno and Daly City and a mid-bay zigzag. However, it is much more complete, extending almost all the way to Berkeley. The android trajectory seems to be closer to the ground truth, but abruptly ends around Duboce/Mission and does not continue during this section
- `backtracking`: intentional backtracking at the foot of Coleman Ave

### Reference trajectory creation components

Given these errors in the control trajectories, we now consider multiple potential algorithms for converting them to reference trajectories. These algorithms represent a tradeoff between correctness and usability. For example, we could choose a really conservative algorithm which would be very likely to be close to ground truth, but only few runs might result in usable reference trajectories.

#### Normalization

Before we compare temporal trajectories, we need to normalize them. This is because the control data is sensed from two separate phones, and the timestamps are different. So we need to align the timestamp trajectories so that we can see how far apart they are. We use a simple normalization in which we linearly interpolate the lat/lng separately at a set of common timestamps. 

**Note**: we have to restrict the common timestamps to the range of input locations for each trajectory. This is because interpolation does not work well, and in cases where the trajectory is incomplete (`temporal_zigzags`) the generated location for the entire missing timestamp range is the final point. We ensure that the timestamps across phone still align by converting them to ints.

#### Distances and projections

In some of the more complex comparisons, we will distance comparisons between trajectories. We use two kinds of potential distances:
1. `projection`: which is the projection of one trajectory on the other
1. `distance`: which is the distance between the two trajectories at a particular point

The comparisons can be between the control trajectories, or between the control trajectories and ground truth

#### Filtering

After computing the distances, we can filter out obviously invalid points. Some validity checks are:

1. `control_trajectories`: points are valid if they are close to each other
1. `ground_truth_both`: points are valid if they are close to the ground truth in both trajectories
1. `ground_truth_either`: points are valid if they are close to the ground truth in either trajectory
1. `distance_along_route`: points are valid if they are further along the ground truth trajectory 

#### Merging

After we compare the trajectories and decide which points to retain, we will potentially have two fairly close-by points. We need to figure out how to combine them into one. Potential options are:
1. random (requires only control trajectories)
1. midpoint (requires only control trajectories)
1. closer to ground truth (requires control trajectories and ground truth)
1. closer to previous distance along route (requires control trajectories and ground truth)

### Candidate algorithms

We combine the components above into the following potential algorithms

#### Control trajectory-only comparisons

Note that in this case, because we interpolate for different ranges, we need to ensure that we are calculating the diff between the same points and not different points. See `train_bus_ebike_mtv_ucb/berkeley_to_mtv_SF_express_bus/ebike_bikeshare_urban_long_1` for an example. The section started at `2019-07-25T16:36:32.386274-07:00`, but on iOS, we did not get any points until 16:36:41, although we had android points right from 16:36:33. This means that we were matching up points at different timestamps, which caused the distance to be larger.

In [17]:
pv_ucb.map()["ios"]["ucb-sdb-ios-1"]["evaluation_ranges"][1]["evaluation_trip_ranges"][2]["location_df"].query("ts > (1564097792 - 15) & ts < (1564097792 + 15)").fmt_time

4272    2019-07-25T16:36:17-0700
4273    2019-07-25T16:36:18-0700
4274    2019-07-25T16:36:19-0700
4275    2019-07-25T16:36:20-0700
4276    2019-07-25T16:36:21-0700
4277    2019-07-25T16:36:22-0700
4278    2019-07-25T16:36:23-0700
4279    2019-07-25T16:36:24-0700
4280    2019-07-25T16:36:25-0700
4281    2019-07-25T16:36:26-0700
4282    2019-07-25T16:36:28-0700
4283    2019-07-25T16:36:41-0700
4284    2019-07-25T16:36:42-0700
4285    2019-07-25T16:36:44-0700
4286    2019-07-25T16:36:45-0700
4287    2019-07-25T16:36:46-0700
Name: fmt_time, dtype: object

In [18]:
pv_ucb.map()["android"]["ucb-sdb-android-1"]["evaluation_ranges"][1]["evaluation_trip_ranges"][2]["location_df"].query("ts > (1564097792 - 15) & ts < (1564097792 + 15)").fmt_time

10599    Jul 25, 2019 4:36:18 PM
10600    Jul 25, 2019 4:36:19 PM
10601    Jul 25, 2019 4:36:20 PM
10602    Jul 25, 2019 4:36:21 PM
10603    Jul 25, 2019 4:36:22 PM
10604    Jul 25, 2019 4:36:23 PM
10605    Jul 25, 2019 4:36:24 PM
10606    Jul 25, 2019 4:36:25 PM
10607    Jul 25, 2019 4:36:26 PM
10608    Jul 25, 2019 4:36:27 PM
10609    Jul 25, 2019 4:36:28 PM
10610    Jul 25, 2019 4:36:29 PM
10611    Jul 25, 2019 4:36:30 PM
10612    Jul 25, 2019 4:36:31 PM
10613    Jul 25, 2019 4:36:32 PM
10614    Jul 25, 2019 4:36:33 PM
10615    Jul 25, 2019 4:36:34 PM
10616    Jul 25, 2019 4:36:35 PM
10617    Jul 25, 2019 4:36:36 PM
10618    Jul 25, 2019 4:36:37 PM
10619    Jul 25, 2019 4:36:38 PM
10620    Jul 25, 2019 4:36:39 PM
10621    Jul 25, 2019 4:36:40 PM
10622    Jul 25, 2019 4:36:41 PM
10623    Jul 25, 2019 4:36:42 PM
10624    Jul 25, 2019 4:36:43 PM
10625    Jul 25, 2019 4:36:44 PM
10626    Jul 25, 2019 4:36:45 PM
10627    Jul 25, 2019 4:36:46 PM
Name: fmt_time, dtype: object

In [19]:
def display_gt_and_reference(entry, loc_df_label, with_points=False):
    print(entry.keys())
    curr_map = folium.Map()
    # print("Using ground truth %s" % entry["ground_truth"]["leg"]["id"])
    gt_leg_gj = ezgj.get_geojson_for_linestring(entry["ground_truth"]["linestring"], color="green")
    gt_leg_gj_feature = folium.GeoJson(gt_leg_gj, name="ground_truth")
    curr_map.add_child(gt_leg_gj_feature)
    if with_points:
        gt_leg_gj_points = ezgj.get_point_markers(gt_leg_gj, name="ground_truth_points", color="green")
        curr_map.add_child(gt_leg_gj_points)
    
    sensed_location_df = entry[loc_df_label]
    # print("Adding section for %s with length %s" % (loc_df_label, len(sensed_location_df)))
    if len(sensed_location_df) > 0:
        sensed_section_gj = gj.Feature(geometry=gj.LineString(coordinates=list(zip(sensed_location_df.longitude, sensed_location_df.latitude))),
                                   properties={"style": {"color": "red"}, "ts": list(sensed_location_df.ts)})
        sensed_leg_gj_feature = folium.GeoJson(sensed_section_gj, name="reference_trajectory")
        print(sensed_leg_gj_feature)
        curr_map.add_child(sensed_leg_gj_feature)
        if with_points:
            sensed_leg_gj_points = ezgj.get_point_markers(sensed_section_gj, name="reference_points", color="red", tz="America/Los_Angeles")
            curr_map.add_child(sensed_leg_gj_points)
    
    add_section_and_points(curr_map, entry["temporal_control"]["android"], "location_df", "android", "orange", with_points)
    add_section_and_points(curr_map, entry["temporal_control"]["ios"], "location_df", "ios", "purple", with_points)
    
    curr_map.fit_bounds(gt_leg_gj_feature.get_bounds())
    folium.LayerControl().add_to(curr_map)
    return curr_map

##### Effect of threshold

For the "good" trajectories (`easiest` and `backtracking`), the threshold has essentially no effect. The trajectories are so good that the tolerance is less than 10 meters and we retain the entire trajectory. For the other two, even if the coverage is good, the quality of the final trajectory is not that great. For example, consider the offset along Hawthorne Ave in the `weird_android` case and the deviations from the ground truth along BART in the `temporal_zigzags` case.

And for the `temporal_zigzags`, at small thresholds, almost nothing matches.

Also, in the case where the data was missing from one of the trajectories (i.e. `temporal_zigzags` on `android`), our reference trajectory also ends, leading to poor coverage compared to the alternatives.

In [20]:
for e in deep_dive_dataset.values():
    e["ct_midpoint_loc_df_10"] = emr.ref_ct_general(e, emr.b_merge_midpoint,
                                               10, tz="America/Los_Angeles")
    e["ct_midpoint_loc_df_25"] = emr.ref_ct_general(e, emr.b_merge_midpoint,
                                               25, tz="America/Los_Angeles")
    e["ct_midpoint_loc_df_50"] = emr.ref_ct_general(e, emr.b_merge_midpoint,
                                               50, tz="America/Los_Angeles")
    e["ct_midpoint_loc_df_100"] = emr.ref_ct_general(e, emr.b_merge_midpoint,
                                               100, tz="America/Los_Angeles")
    e["dtw_no_gt"] = emr.ref_dtw_no_gt_with_ends_general(e, tz="America/Los_Angeles")

After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 809 -> 565
After filtering against polygons 2, 667 -> 507
After filtering, retained 543 of 563 (0.9644760213143873)
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 809 -> 565
After filtering against polygons 2, 667 -> 507
After filtering, retained 559 of 563 (0.9928952042628775)
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 809 -> 565
After filtering against polygons 2, 667 -> 507
After filtering, retained 559 of 563 (0.9928952042628775)
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 809 -> 565
After filtering against polygons 2, 667 -> 507
After filtering, retained 559 of 563 (0.9928952042628775)
After filtering against polygons

In [21]:
evaluation_maps = bre.Figure()
test_candidates = ["ct_midpoint_loc_df_10", "ct_midpoint_loc_df_25", "ct_midpoint_loc_df_50", "ct_midpoint_loc_df_100", "dtw_no_gt"]
nRows = len(test_candidates)
for i, c in enumerate(test_candidates):
    evaluation_maps.add_child(bre.Html(c))
    map_list = [display_gt_and_reference(e, c) for e in deep_dive_dataset.values()]    
    for j, curr_map in enumerate(map_list):
        evaluation_maps.add_subplot(nRows, 4, 4*i+(j+1)).add_child(curr_map)
evaluation_maps

dict_keys(['ground_truth', 'temporal_control', 'ct_midpoint_loc_df_10', 'ct_midpoint_loc_df_25', 'ct_midpoint_loc_df_50', 'ct_midpoint_loc_df_100', 'dtw_no_gt'])
Adding section for android with length 809
Adding section for ios with length 667
dict_keys(['ground_truth', 'temporal_control', 'ct_midpoint_loc_df_10', 'ct_midpoint_loc_df_25', 'ct_midpoint_loc_df_50', 'ct_midpoint_loc_df_100', 'dtw_no_gt'])
Adding section for android with length 467
Adding section for ios with length 718
dict_keys(['ground_truth', 'temporal_control', 'ct_midpoint_loc_df_10', 'ct_midpoint_loc_df_25', 'ct_midpoint_loc_df_50', 'ct_midpoint_loc_df_100', 'dtw_no_gt'])
Adding section for android with length 749
Adding section for ios with length 404
dict_keys(['ground_truth', 'temporal_control', 'ct_midpoint_loc_df_10', 'ct_midpoint_loc_df_25', 'ct_midpoint_loc_df_50', 'ct_midpoint_loc_df_100', 'dtw_no_gt'])
Adding section for android with length 1207
Adding section for ios with length 1016
dict_keys(['ground_tru

##### Effect of merge function

Again, for the "good" trajectories (`easiest` and `backtracking`), the merge function has essentially no effect. The trajectories are so good that the tolerance is less than 10 meters and using the midpoint versus random versus closest makes no difference.

For the other two, choosing the closest point allows us to handle the case where the errors are related primarily to one phone (e.g. in the `weird_android` case). So if the iOS trajectory is good (as determined by a comparison with spatial ground truth), we can use it directly and not have it be polluted by the bad android trajectory.

So effectively, with this approach, we are choosing the good points from each of the trajectories and stitching them together to create an overall trajectory. This implies that we cannot use an inner join for the merge, since then we would only retain points that were good in **both** trajectories. We use an outer join instead, and if there are points that are good only in one trajectory, we just select them.

Note that this allows us to use much smaller thresholds and still get coverages similar to the higher thresholds while using midpoints

However, stitching together points from multiple trajectories is challenging if there are time sychronization issues. While the timestamps for a single phone are guaranteed to be consistent, timestamps across phones are not guaranteed to be consistent, and flip flopping between phones can lead to zigzags in the final trajectories. For example, in the `weird_android` case, see:
- the section of Springer between Todd and El Monte,
- the intersection of El Camino and Shoreline,
- El Monte near Mayer Court

In [22]:
import importlib
importlib.reload(emr)

<module 'emeval.metrics.reference_trajectory' from '/Users/kinjal/Code/openpath/mobilitynet-analysis-scripts/emeval/metrics/reference_trajectory.py'>

In [23]:
for e in deep_dive_dataset.values():
    e["ct_closer_gt_dist_10"] = emr.ref_gt_general(e, emr.b_merge_closer_gt_dist,
                                               10, tz="America/Los_Angeles")
    e["ct_closer_gt_dist_25"] = emr.ref_gt_general(e, emr.b_merge_closer_gt_dist,
                                               25, tz="America/Los_Angeles")
    e["dtw_gt"] = emr.ref_dtw_gt_with_ends_general(e, points_per_second=1, interp=2, tz="America/Los_Angeles")
    # e["dtw_gt_1"] = emr.ref_dtw_gt_with_ends_general(e, points_per_second=1, interp=1, tz="America/Los_Angeles")
    # e["dtw_gt_0"] = emr.ref_dtw_gt_with_ends_general(e, points_per_second=1, interp=0, tz="America/Los_Angeles")
    # e["dtw_gt_-1"] = emr.ref_dtw_gt_with_ends_general(e, points_per_second=1, interp=-1, tz="America/Los_Angeles")
    # e["dtw_gt_0.3"] = emr.ref_dtw_gt_with_ends_general(e, points_per_second=0.3, interp=2, tz="America/Los_Angeles")

After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 809 -> 565
After filtering against polygons 2, 667 -> 507
After filtering, 560 of 563 (0.9946714031971581) for android and 559 of 559 (1.0) for ios
After merging, found 560 of android 563 (0.9946714031971581), ios 559 (1.0017889087656529)
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 809 -> 565
After filtering against polygons 2, 667 -> 507
After filtering, 562 of 563 (0.9982238010657194) for android and 559 of 559 (1.0) for ios
After merging, found 562 of android 563 (0.9982238010657194), ios 559 (1.0053667262969588)
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 78 -> 74


/Users/kinjal/Code/openpath/mobilitynet-analysis-scripts/emeval/metrics/reference_trajectory.py:654: RuntimeWarning: divide by zero encountered in scalar divide
  speed.append(dist / (gpdf.iloc[idx].ts - gpdf.iloc[idx-1].ts))
/Users/kinjal/Code/openpath/mobilitynet-analysis-scripts/emeval/metrics/reference_trajectory.py:656: RuntimeWarning: invalid value encountered in scalar subtract
  acceleration.append((speed[idx-1] - speed[idx-2]) / (gpdf.iloc[idx-1].ts - gpdf.iloc[idx-2].ts))


After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 467 -> 180
After filtering against polygons 2, 718 -> 533
After filtering, 220 of 666 (0.3303303303303303) for android and 594 of 621 (0.9565217391304348) for ios
After merging, found 603 of android 666 (0.9054054054054054), ios 621 (0.9710144927536232)
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 467 -> 180
After filtering against polygons 2, 718 -> 533
After filtering, 425 of 666 (0.6381381381381381) for android and 621 of 621 (1.0) for ios
After merging, found 622 of android 666 (0.933933933933934), ios 621 (1.001610305958132)
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 78 -> 74


/Users/kinjal/Code/openpath/mobilitynet-analysis-scripts/emeval/metrics/reference_trajectory.py:654: RuntimeWarning: divide by zero encountered in scalar divide
  speed.append(dist / (gpdf.iloc[idx].ts - gpdf.iloc[idx-1].ts))
/Users/kinjal/Code/openpath/mobilitynet-analysis-scripts/emeval/metrics/reference_trajectory.py:656: RuntimeWarning: invalid value encountered in scalar subtract
  acceleration.append((speed[idx-1] - speed[idx-2]) / (gpdf.iloc[idx-1].ts - gpdf.iloc[idx-2].ts))


After filtering against polygons 2, 624 -> 621
After filtering against polygons 2, 624 -> 621
After filtering against polygons 2, 749 -> 749
After filtering against polygons 2, 404 -> 404
After filtering, 641 of 1775 (0.3611267605633803) for android and 194 of 3239 (0.059895029330040137) for ios
After merging, found 785 of android 1775 (0.4422535211267606), ios 3239 (0.24235875270145107)
After filtering against polygons 2, 624 -> 621
After filtering against polygons 2, 624 -> 621
After filtering against polygons 2, 749 -> 749
After filtering against polygons 2, 404 -> 404
After filtering, 754 of 1775 (0.4247887323943662) for android and 686 of 3239 (0.21179376350725532) for ios
After merging, found 1161 of android 1775 (0.6540845070422535), ios 3239 (0.3584439641864773)
After filtering against polygons 2, 624 -> 621
After filtering against polygons 2, 624 -> 621


/Users/kinjal/Code/openpath/mobilitynet-analysis-scripts/emeval/metrics/reference_trajectory.py:654: RuntimeWarning: divide by zero encountered in scalar divide
  speed.append(dist / (gpdf.iloc[idx].ts - gpdf.iloc[idx-1].ts))
/Users/kinjal/Code/openpath/mobilitynet-analysis-scripts/emeval/metrics/reference_trajectory.py:656: RuntimeWarning: invalid value encountered in scalar subtract
  acceleration.append((speed[idx-1] - speed[idx-2]) / (gpdf.iloc[idx-1].ts - gpdf.iloc[idx-2].ts))
/Users/kinjal/Code/openpath/mobilitynet-analysis-scripts/emeval/metrics/reference_trajectory.py:654: RuntimeWarning: invalid value encountered in scalar divide
  speed.append(dist / (gpdf.iloc[idx].ts - gpdf.iloc[idx-1].ts))


After filtering against polygons 2, 53 -> 48
After filtering against polygons 2, 53 -> 48
After filtering against polygons 2, 1207 -> 1182
After filtering against polygons 2, 1016 -> 1001
After filtering, 1035 of 1181 (0.8763759525825572) for android and 900 of 1183 (0.760777683854607) for ios
After merging, found 1089 of android 1181 (0.9220999153259949), ios 1183 (0.9205409974640744)
After filtering against polygons 2, 53 -> 48
After filtering against polygons 2, 53 -> 48
After filtering against polygons 2, 1207 -> 1182
After filtering against polygons 2, 1016 -> 1001
After filtering, 1181 of 1181 (1.0) for android and 1183 of 1183 (1.0) for ios
After merging, found 1185 of android 1181 (1.0033869602032177), ios 1183 (1.0016906170752324)
After filtering against polygons 2, 53 -> 48
After filtering against polygons 2, 53 -> 48


/Users/kinjal/Code/openpath/mobilitynet-analysis-scripts/emeval/metrics/reference_trajectory.py:654: RuntimeWarning: divide by zero encountered in scalar divide
  speed.append(dist / (gpdf.iloc[idx].ts - gpdf.iloc[idx-1].ts))
/Users/kinjal/Code/openpath/mobilitynet-analysis-scripts/emeval/metrics/reference_trajectory.py:654: RuntimeWarning: invalid value encountered in scalar divide
  speed.append(dist / (gpdf.iloc[idx].ts - gpdf.iloc[idx-1].ts))
/Users/kinjal/Code/openpath/mobilitynet-analysis-scripts/emeval/metrics/reference_trajectory.py:656: RuntimeWarning: invalid value encountered in scalar subtract
  acceleration.append((speed[idx-1] - speed[idx-2]) / (gpdf.iloc[idx-1].ts - gpdf.iloc[idx-2].ts))


In [24]:
import pickle

def save_deep_dive_dataset(deep_dive_dataset, filename='deep_dive_dataset.pkl'):
    """
    Save the deep_dive_dataset to a file using pickle.
    
    Args:
        deep_dive_dataset: The dataset to save
        filename: Output filename (default: 'deep_dive_dataset.pkl')
    """
    with open(filename, 'wb') as f:
        pickle.dump(deep_dive_dataset, f)
    print(f"deep_dive_dataset saved to {filename}")

# Call the function with the current deep_dive_dataset
save_deep_dive_dataset(deep_dive_dataset)

deep_dive_dataset saved to deep_dive_dataset.pkl


In [25]:
evaluation_maps = bre.Figure()
test_candidates = ["ct_closer_gt_dist_10", "ct_closer_gt_dist_25", "dtw_gt"] #"ct_midpoint_loc_df_50", "dtw_gt"]#, "dtw_gt_1", "dtw_gt_0", "dtw_gt_-1", "dtw_gt_0.3"]
nRows = len(test_candidates)
for i, c in enumerate(test_candidates):
    evaluation_maps.add_child(bre.Html(c))
    map_list = [display_gt_and_reference(e, c) for e in deep_dive_dataset.values()]    
    for j, curr_map in enumerate(map_list):
        evaluation_maps.add_subplot(nRows, 4, 4*i+(j+1)).add_child(curr_map)
evaluation_maps

dict_keys(['ground_truth', 'temporal_control', 'ct_midpoint_loc_df_10', 'ct_midpoint_loc_df_25', 'ct_midpoint_loc_df_50', 'ct_midpoint_loc_df_100', 'dtw_no_gt', 'ct_closer_gt_dist_10', 'ct_closer_gt_dist_25', 'dtw_gt'])
Adding section for android with length 809
Adding section for ios with length 667
dict_keys(['ground_truth', 'temporal_control', 'ct_midpoint_loc_df_10', 'ct_midpoint_loc_df_25', 'ct_midpoint_loc_df_50', 'ct_midpoint_loc_df_100', 'dtw_no_gt', 'ct_closer_gt_dist_10', 'ct_closer_gt_dist_25', 'dtw_gt'])
Adding section for android with length 467
Adding section for ios with length 718
dict_keys(['ground_truth', 'temporal_control', 'ct_midpoint_loc_df_10', 'ct_midpoint_loc_df_25', 'ct_midpoint_loc_df_50', 'ct_midpoint_loc_df_100', 'dtw_no_gt', 'ct_closer_gt_dist_10', 'ct_closer_gt_dist_25', 'dtw_gt'])
Adding section for android with length 749
Adding section for ios with length 404
dict_keys(['ground_truth', 'temporal_control', 'ct_midpoint_loc_df_10', 'ct_midpoint_loc_df_25

In [26]:
import emeval.metrics.movie as emm

# [emm.create_route_animation(e["dtw_gt"], timestamp_col="ts", fps=10, output_folder="dtw_gt_frames", output_filename="dtw_gt.mp4") for e in deep_dive_dataset.values()]

##### Incorporating _forward motion_

We can handle the time synchronization issues by ensuring that travel only occurs "forward" along the ground truth trajectory. We can determine the distance travelled so far as a projection of the control trajectory along the ground truth and only incorporate points that make forward progress. Note that this requires the use of a global variable to track the distance so far, and the merging function is no longer stateless.

And, as feared, in the place where there is a genuine backtrack (`backtracking` use case at Market and Devine), we trim some of the backtrack.

In [27]:
importlib.reload(emr)

<module 'emeval.metrics.reference_trajectory' from '/Users/kinjal/Code/openpath/mobilitynet-analysis-scripts/emeval/metrics/reference_trajectory.py'>

In [28]:
for e in deep_dive_dataset.values():
    e["travel_forward_10"] = emr.ref_travel_forward(e, 10, tz="America/Los_Angeles")
    e["travel_forward_25"] = emr.ref_travel_forward(e, 25, tz="America/Los_Angeles")
    e["travel_forward_50"] = emr.ref_travel_forward(e, 50, tz="America/Los_Angeles")

After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 809 -> 565
After filtering against polygons 2, 667 -> 507
After filtering, 560 of 563 (0.9946714031971581) for android and 559 of 559 (1.0) for ios
After merging, found 527 / 560 of android 563 (0.9360568383658969), ios 559 (0.9427549194991055)
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 809 -> 565
After filtering against polygons 2, 667 -> 507
After filtering, 562 of 563 (0.9982238010657194) for android and 559 of 559 (1.0) for ios
After merging, found 527 / 562 of android 563 (0.9360568383658969), ios 559 (0.9427549194991055)
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 78 -> 74
After filtering against polygons 2, 809 -> 565
After filtering against polygons 2, 667 -> 507
After filtering, 563 of 563 (1.0) for android and 559 of 559 (1.0) for ios

In [29]:
evaluation_maps = bre.Figure()
test_candidates = ["travel_forward_10", "travel_forward_25", "travel_forward_50"]
nRows = len(test_candidates)
for i, c in enumerate(test_candidates):
    evaluation_maps.add_child(bre.Html(c))
    map_list = [display_gt_and_reference(e, c) for e in deep_dive_dataset.values()]    
    for j, curr_map in enumerate(map_list):
        evaluation_maps.add_subplot(nRows, 4, 4*i+(j+1)).add_child(curr_map)
evaluation_maps

dict_keys(['ground_truth', 'temporal_control', 'ct_midpoint_loc_df_10', 'ct_midpoint_loc_df_25', 'ct_midpoint_loc_df_50', 'ct_midpoint_loc_df_100', 'dtw_no_gt', 'ct_closer_gt_dist_10', 'ct_closer_gt_dist_25', 'dtw_gt', 'travel_forward_10', 'travel_forward_25', 'travel_forward_50'])
Adding section for android with length 809
Adding section for ios with length 667
dict_keys(['ground_truth', 'temporal_control', 'ct_midpoint_loc_df_10', 'ct_midpoint_loc_df_25', 'ct_midpoint_loc_df_50', 'ct_midpoint_loc_df_100', 'dtw_no_gt', 'ct_closer_gt_dist_10', 'ct_closer_gt_dist_25', 'dtw_gt', 'travel_forward_10', 'travel_forward_25', 'travel_forward_50'])
Adding section for android with length 467
Adding section for ios with length 718
dict_keys(['ground_truth', 'temporal_control', 'ct_midpoint_loc_df_10', 'ct_midpoint_loc_df_25', 'ct_midpoint_loc_df_50', 'ct_midpoint_loc_df_100', 'dtw_no_gt', 'ct_closer_gt_dist_10', 'ct_closer_gt_dist_25', 'dtw_gt', 'travel_forward_10', 'travel_forward_25', 'travel_f

### Estimating the coverage of reference trajectories

- The `ct_midpoint` methods do not require ground truth, do not generate zigzags and work well with backtracking. Their main drawback is that they work well only for very high quality trajectories.
- The `forward_motion` method works well even with poor quality trajectories and gives great coverage but does not handle backtracking and requires valid ground truth, so it will not work within the start_end polygons

Since we know that we do not have even spatial ground truth within the start and end polygons, we will only evaluate the algorithms on the subset of the points (both sensed and ground truth) outside of the polygons.

In [30]:
def get_reference_trajectory_tree(pv):
    ref_tree = {}
    # This is a GeoSeries
    
    for phone_os, phone_map in pv.map().items():
        for phone_label, phone_detail_map in phone_map.items():
            for (r_idx, r) in enumerate(phone_detail_map["evaluation_ranges"]):
                if r["eval_role_base"] != "accuracy_control":
                    continue
                for (tr_idx, tr) in enumerate(r["evaluation_trip_ranges"]):
                    for (sr_idx, sr) in enumerate(tr["evaluation_section_ranges"]):
                        # This is a Shapely LineString
                        section_gt_leg = pv.spec_details.get_ground_truth_for_leg(tr["trip_id_base"], sr["trip_id_base"], sr["start_ts"], sr["end_ts"])
                        section_gt_shapes = gpd.GeoSeries(eisd.SpecDetails.get_shapes_for_leg(section_gt_leg))
                        if len(section_gt_shapes) == 1:
                            print("No ground truth route for %s %s, must be polygon, skipping..." % (tr["trip_id_base"], sr["trip_id_base"]))
                            assert section_gt_leg["type"] != "TRAVEL", "For %s, %s, %s, %s, %s found type %s" % (phone_os, phone_label, r_idx, tr_idx, sr_idx, section_gt_leg["type"])
                            continue
                        if len(sr['location_df']) == 0:
                            print("No sensed locations found, role = %s skipping..." % (r["eval_role_base"]))
                            # assert r["eval_role_base"] == "power_control", "Found no locations for %s, %s, %s, %s, %s" % (phone_os, phone_label, r_idx, tr_idx, sr_idx)
                            continue
                        
                        sec_name = tr["trip_id_base"] + "/" + sr["trip_id_base"] + "_" + str(r_idx)
                        if sec_name not in ref_tree:
                            ref_tree[sec_name] = {
                                "trip_id": tr["trip_id_base"],
                                "section_id": sr["trip_id_base"],
                                "run": r_idx,
                                "ground_truth": {
                                    "leg": section_gt_leg
                                }
                            }
                        
                        assert sec_name in ref_tree
                        e = ref_tree[sec_name]
                        if "temporal_control" not in e:
                            e["temporal_control"] = {}
                            e["start_ts"] = sr["start_ts"]
                            e["end_ts"] = sr["end_ts"]
                        e["temporal_control"][phone_os] = sr
    return ref_tree
                        
def fill_ref_tree_entry(e):
    print("Considering entry %s %s %s" % (e["trip_id"], e["section_id"], e["run"]))
    curr_tz = "America/Los_Angeles"
    assert "android" in e["temporal_control"] and "ios" in e["temporal_control"]
    # The functions convert both the input values and the ground truth to UTM before calculating the distances
    # So the "latitude" and "longitude" here is actually in meters and the points can't be displayed directly
    # TODO: figure out the best way to support both
    e["travel_forward_25"] = emr.ref_travel_forward(e, 25, tz=curr_tz)
    e["travel_forward_50"] = emr.ref_travel_forward(e, 50, tz=curr_tz)
    e["ct_midpoint_25"] = emr.ref_ct_general(e, emr.b_merge_midpoint, 25, tz=curr_tz)
    e["ct_midpoint_50"] = emr.ref_ct_general(e, emr.b_merge_midpoint, 50, tz=curr_tz)

def get_coverage(pv, ref_tree):
    spatial_error_list = []
    for e in ref_tree.values():
        # we resample every second, so full coverage would involve 1 entry for each second in the section
        # If we have less than that, the length of the dataframe will be less
        spatial_error_base = {"timeline": pv.spec_details.curr_spec["id"],
                         "trip_id": e["trip_id"], "section_id": e["section_id"], "run": e["run"]}
        
        for result in ["travel_forward_25", "travel_forward_50", "ct_midpoint_25", "ct_midpoint_50"]:
            spatial_error = copy.copy(spatial_error_base)
            spatial_error["algo"] = result
            spatial_error["coverage_density"] = emr.coverage_density(e[result], e)
            spatial_error["coverage_time"] = emr.coverage_time(e[result], e)
            spatial_error["coverage_max_gap"] = emr.coverage_max_gap(e[result], e)
            spatial_error_list.append(spatial_error)
    return spatial_error_list

def get_reference_coverage(pv, ref_tree_root):
    ref_tree = get_reference_trajectory_tree(pv)
    ref_tree_root[pv.spec_details.curr_spec["id"]] = ref_tree
    [fill_ref_tree_entry(e) for e in ref_tree.values()]
    return get_coverage(pv, ref_tree)

In [31]:
importlib.reload(emr)

<module 'emeval.metrics.reference_trajectory' from '/Users/kinjal/Code/openpath/mobilitynet-analysis-scripts/emeval/metrics/reference_trajectory.py'>

In [32]:
ref_tree = {}
coverage_list = []
# coverage_list.extend(get_reference_coverage(pv_la, ref_tree))
# coverage_list.extend(get_reference_coverage(pv_sj, ref_tree))
coverage_list.extend(get_reference_coverage(pv_ucb, ref_tree))

coverage_df = pd.DataFrame(coverage_list)

No ground truth route for mtv_to_berkeley_sf_bart wait_for_commuter_rail_aboveground, must be polygon, skipping...
No ground truth route for mtv_to_berkeley_sf_bart tt_commuter_rail_aboveground_subway_underground, must be polygon, skipping...
No ground truth route for mtv_to_berkeley_sf_bart wait_for_subway_underground, must be polygon, skipping...
No ground truth route for mtv_to_berkeley_sf_bart wait_for_city_bus_short, must be polygon, skipping...
No ground truth route for mtv_to_berkeley_sf_bart walk_end, must be polygon, skipping...
No ground truth route for berkeley_to_mtv_SF_express_bus tt_ebike_bikeshare_urban_long_express_bus, must be polygon, skipping...
No ground truth route for berkeley_to_mtv_SF_express_bus wait_for_express_bus, must be polygon, skipping...
No ground truth route for berkeley_to_mtv_SF_express_bus wait_for_light_rail_below_above_ground, must be polygon, skipping...
No ground truth route for berkeley_to_mtv_SF_express_bus tt_light_rail_below_above_ground_com

NotImplementedError: cannot perform cumsum with type geometry

In [ ]:
coverage_df.head()

In [ ]:
timeline_list = ["car_scooter_brex_san_jose", "unimodal_trip_car_bike_mtv_la"]
test_candidates = ["ct_midpoint_25", "ct_midpoint_50", "travel_forward_25", "travel_forward_50"]
for i, tl in enumerate(timeline_list):
    unique_sections = pd.Series(coverage_df.query("timeline == @tl").section_id.unique())
    ifig, ax_array = plt.subplots(nrows=len(unique_sections),ncols=3,figsize=(10,10), sharex=True, sharey=True)
    for j, sid in enumerate(unique_sections):
        coverage_df.query("timeline == @tl & section_id == @sid").boxplot(ax = ax_array[j][0], column=["coverage_density"], by=["algo"], showbox=False, whis="range")
        coverage_df.query("timeline == @tl & section_id == @sid").boxplot(ax = ax_array[j][1], column=["coverage_time"], by=["algo"], showbox=False, whis="range")
        coverage_df.query("timeline == @tl & section_id == @sid").boxplot(ax = ax_array[j][2], column=["coverage_max_gap"], by=["algo"], showbox=False, whis="range")
        ax_array[j][0].set_ylabel(sid)
        for k in range(3):
            if j != 0:
                ax_array[j][k].set_title("")
            ax_array[j][k].set_xlabel("")
            
    for k in range(3):
        ax_array[len(unique_sections)-1][k].set_xticklabels(["ctm_25", "ctm_50", "tf_25", "tf_50"])
    ifig.suptitle(tl)

In [ ]:
long_timeline = "train_bus_ebike_mtv_ucb"
test_candidates = ["ct_midpoint_25", "ct_midpoint_50", "travel_forward_25", "travel_forward_50"]

unique_sections = pd.Series(coverage_df.query("timeline == @long_timeline").section_id.unique())
nRows = len(unique_sections)
ifig,ax_array = plt.subplots(nrows=nRows, ncols=3,  figsize=(6,45), sharex=True, sharey=True)
for i, sid in enumerate(unique_sections):
    coverage_df.query("timeline == @long_timeline & section_id == @sid").boxplot(ax = ax_array[i][0], column=["coverage_density"], by=["algo"], showbox=False, whis="range")
    coverage_df.query("timeline == @long_timeline & section_id == @sid").boxplot(ax = ax_array[i][1], column=["coverage_time"], by=["algo"], showbox=False, whis="range")
    coverage_df.query("timeline == @long_timeline & section_id == @sid").boxplot(ax = ax_array[i][2], column=["coverage_max_gap"], by=["algo"], showbox=False, whis="range")
    ax_array[i][0].set_ylabel(sid)
    for k in range(3):
        if i != 0:
            ax_array[i][k].set_title("")
        ax_array[i][k].set_xlabel("")

for i in range(0,2):
    ax_array[nRows-1][i].set_xticklabels(["ctm_25", "ctm_50", "tf_25", "tf_50"])
    
ifig.suptitle(long_timeline, y=0.92)
# ifig

### Filling in the gaps with more resampling

As we can see, even when coverage density is low, there are not many large gaps in the data, specially with the `tf` methods. There is only one case with a gap > 20% for the `tf` algorithm, and that is one of the light rail runs. Since we know the spatial ground truth for the missing points, we can reconstruct the spatio-temporal ground truth by interpolating the points. This is not going to be perfect, but it will allow us to compare the complete trajectories instead of partial trajectories.

In [ ]:
# Really bad data points
outliers = coverage_df[(coverage_df.coverage_density < 0.5) & (coverage_df.coverage_time < 0.5)]; outliers

### Outlier verification

We now briefly evaluate the outliers along each of the metrics above.

#### Density outliers

In [ ]:
importlib.reload(ezgj)

In [ ]:
#### travel_forward_25 	0.166812 	2 	walk to the bikeshare location 	train_bus_ebike_mtv_ucb 	berkeley_to_mtv_SF_express_bus
# This is because of walking around to find the bicycle, and the fact that we don't strip out the points within the polygons any more
sel_name = "berkeley_to_mtv_SF_express_bus/walk to the bikeshare location_2"
e = ref_tree["train_bus_ebike_mtv_ucb"][sel_name]
fig = bre.Figure()
fig.add_subplot(1,2,1).add_child(display_gt_and_reference(e, "travel_forward_25", with_points=True))
fig.add_subplot(1,2,2).add_child(display_gt_and_reference(e, "ct_midpoint_25", with_points=True))

In [ ]:
# ct_midpoint_25 	0.017705 	0.068073 	0 	subway_underground 	train_bus_ebike_mtv_ucb 	mtv_to_berkeley_sf_bart
# This is just messed up and unusable
sel_name = "mtv_to_berkeley_sf_bart/subway_underground_0"
e = ref_tree["train_bus_ebike_mtv_ucb"][sel_name]
fig = bre.Figure()
fig.add_subplot(1,2,1).add_child(display_gt_and_reference(e, "travel_forward_25", with_points=True))
fig.add_subplot(1,2,2).add_child(display_gt_and_reference(e, "ct_midpoint_25", with_points=True))

#### Now let's spot check some of the values where the density is significatly different from the time range

The problem here is that these are actually not that terrible. Even in the case where the coverage density is  0.070792, we could probably reconstruct it enough to work. The real problem is how well those points are distributed = whether there are large gaps. Let's see if we can use that angle instead.

In [ ]:
# outliers = coverage_df.query("section_id == 'subway_underground' & (algo == 'travel_forward_25' | algo == 'ct_midpoint_25')"); outliers
outliers = coverage_df[(coverage_df.coverage_density - coverage_df.coverage_time).abs() > 0.85]; outliers

In [ ]:
# ct_midpoint_25 	0.070792 	0.998652 	1 	commuter_rail_with_tunnels 	train_bus_ebike_mtv_ucb 	berkeley_to_mtv_SF_express_bus
sel_name = "berkeley_to_mtv_SF_express_bus/commuter_rail_with_tunnels_1"
e = ref_tree["train_bus_ebike_mtv_ucb"][sel_name]
fig = bre.Figure()
fig.add_subplot(1,2,1).add_child(display_gt_and_reference(e, "travel_forward_25", with_points=True))
fig.add_subplot(1,2,2).add_child(display_gt_and_reference(e, "ct_midpoint_25", with_points=True))

In [ ]:
# ct_midpoint_25 	0.024405 	0.881352 	2 	subway_underground 	train_bus_ebike_mtv_ucb 	mtv_to_berkeley_sf_bart
sel_name = "mtv_to_berkeley_sf_bart/subway_underground_2"
e = ref_tree["train_bus_ebike_mtv_ucb"][sel_name]
fig = bre.Figure()
fig.add_subplot(1,2,1).add_child(display_gt_and_reference(e, "travel_forward_25", with_points=True))
fig.add_subplot(1,2,2).add_child(display_gt_and_reference(e, "ct_midpoint_25", with_points=True))

In [ ]:
#### travel_forward_25 	0.565114 	1 	commuter_rail_with_tunnels 	train_bus_ebike_mtv_ucb 	berkeley_to_mtv_SF_express_bus
# In this case, the android trajectory is correct, but the iOS trajectory is all over the place, with lots of zigzags, gaps and other wierdnesses.

sel_name = "berkeley_to_mtv_SF_express_bus/commuter_rail_with_tunnels_1"
e = ref_tree["train_bus_ebike_mtv_ucb"][sel_name]
fig = bre.Figure()
fig.add_subplot(1,3,1).add_child(display_gt_and_reference(e, "travel_forward_25", with_points=True))
fig.add_subplot(1,3,2).add_child(display_gt_and_reference(e, "ct_midpoint_25", with_points=True))
fig.add_subplot(1,3,3).add_child(display_gt_and_controls(e, "location_df", with_points=True))

In [ ]:
#### travel_forward_25 	0.276315 	2 	light_rail_below_above_ground 	train_bus_ebike_mtv_ucb 	berkeley_to_mtv_SF_express_bus

# In this case, there is a time mismatch, so adjacent points are separated by ~ 6 seconds.
# e.g. at around Embarcadero and Bryant, the android point is `2019-07-26 18:15:18` while the iOS point is `2019-07-26 18:15:24`. The android point that matches `2019-07-26 18:15:24` is halfway down the block.
sel_name = "berkeley_to_mtv_SF_express_bus/light_rail_below_above_ground_2"
e = ref_tree["train_bus_ebike_mtv_ucb"][sel_name]
fig = bre.Figure()
fig.add_subplot(1,3,1).add_child(display_gt_and_reference(e, "travel_forward_25", with_points=True))
fig.add_subplot(1,3,2).add_child(display_gt_and_reference(e, "ct_midpoint_25", with_points=True))
fig.add_subplot(1,3,3).add_child(display_gt_and_controls(e, "location_df", with_points=True))

In [ ]:
# travel_forward_25 	0.350489 	1 	walk_to_bus 	train_bus_ebike_mtv_ucb 	mtv_to_berkeley_sf_bart
sel_name = "mtv_to_berkeley_sf_bart/walk_to_bus_1"
e = ref_tree["train_bus_ebike_mtv_ucb"][sel_name]
fig = bre.Figure()
fig.add_subplot(1,3,1).add_child(display_gt_and_reference(e, "travel_forward_25", with_points=True))
fig.add_subplot(1,3,2).add_child(display_gt_and_reference(e, "ct_midpoint_25", with_points=True))
fig.add_subplot(1,3,3).add_child(display_gt_and_controls(e, "location_df", with_points=True))

In [ ]:
# travel_forward_25 	0.845444 	0 	freeway_driving_weekday 	car_scooter_brex_san_jose 	freeway_driving_weekday
sel_name = "freeway_driving_weekday/freeway_driving_weekday_0"
e = ref_tree["car_scooter_brex_san_jose"][sel_name]
fig = bre.Figure()
fig.add_subplot(1,3,1).add_child(display_gt_and_reference(e, "travel_forward_25", with_points=True))
fig.add_subplot(1,3,2).add_child(display_gt_and_reference(e, "ct_midpoint_25", with_points=True))
fig.add_subplot(1,3,3).add_child(display_gt_and_controls(e, "location_df", with_points=True))

In [ ]:
# #### travel_forward_25 	0.565114 	1 	commuter_rail_with_tunnels 	train_bus_ebike_mtv_ucb 	berkeley_to_mtv_SF_express_bus
sel_name = "mtv_to_berkeley_sf_bart/subway_underground_0"
e = ref_tree["train_bus_ebike_mtv_ucb"][sel_name]
fig = bre.Figure()
fig.add_subplot(1,3,1).add_child(display_gt_and_reference(e, "travel_forward_25", with_points=True))
fig.add_subplot(1,3,2).add_child(display_gt_and_reference(e, "ct_midpoint_25", with_points=True))
fig.add_subplot(1,3,3).add_child(display_gt_and_controls(e, "location_df", with_points=True))

### Points with large gaps

Finally, we look through outliers with large gaps

In [ ]:
# Really bad data points
import scipy.stats as sps
outliers = coverage_df[(sps.zscore(coverage_df.coverage_max_gap) > 3)]; outliers

In [ ]:
travel_forward_25 = coverage_df.query("algo == 'travel_forward_25'")
travel_forward_25[(sps.zscore(travel_forward_25.coverage_max_gap) > 3)]

In [ ]:
##### travel_forward_25 	0.376220 	0.426081 	0.897489 	2 	walk_to_bus 	train_bus_ebike_mtv_ucb 	mtv_to_berkeley_sf_bart
# Another walk to bus 
sel_name = "mtv_to_berkeley_sf_bart/walk_to_bus_2"
e = ref_tree["train_bus_ebike_mtv_ucb"][sel_name]
fig = bre.Figure()
fig.add_subplot(1,3,1).add_child(display_gt_and_reference(e, "travel_forward_25", with_points=True))
fig.add_subplot(1,3,2).add_child(display_gt_and_reference(e, "ct_midpoint_25", with_points=True))
fig.add_subplot(1,3,3).add_child(display_gt_and_controls(e, "location_df", with_points=True))

In [ ]:
travel_forward_25 = coverage_df.query("algo == 'travel_forward_25' & section_id != 'walk_to_bus'")
travel_forward_25[(sps.zscore(travel_forward_25.coverage_max_gap) > 3)]

In [ ]:
##### travel_forward_25 	0.276315 	0.345167 	0.859747 	2 	light_rail_below_above_ground 	train_bus_ebike_mtv_ucb 	berkeley_to_mtv_SF_express_bus
# Light rail is missing a bunch of initial points because android is just all over the map, and the iOS points are just a little too far away from the ground truth
sel_name = "berkeley_to_mtv_SF_express_bus/light_rail_below_above_ground_2"
e = ref_tree["train_bus_ebike_mtv_ucb"][sel_name]
fig = bre.Figure()
fig.add_subplot(1,3,1).add_child(display_gt_and_reference(e, "travel_forward_25", with_points=True))
fig.add_subplot(1,3,2).add_child(display_gt_and_reference(e, "ct_midpoint_25", with_points=True))
fig.add_subplot(1,3,3).add_child(display_gt_and_controls(e, "location_df", with_points=True))

In [ ]:
ct_midpoint_25 = coverage_df.query("algo == 'ct_midpoint_25'")
ct_midpoint_25[(sps.zscore(ct_midpoint_25.coverage_max_gap) > 2)]

In [ ]:
##### ct_midpoint_25 	0.121904 	0.679046 	0.943681 	1 	subway_underground 	train_bus_ebike_mtv_ucb 	mtv_to_berkeley_sf_bart
# subway, trajectory based is bad, nothing to be done
sel_name = "mtv_to_berkeley_sf_bart/subway_underground_1"
e = ref_tree["train_bus_ebike_mtv_ucb"][sel_name]
fig = bre.Figure()
fig.add_subplot(1,3,1).add_child(display_gt_and_reference(e, "travel_forward_25", with_points=True))
fig.add_subplot(1,3,2).add_child(display_gt_and_reference(e, "ct_midpoint_25", with_points=True))
fig.add_subplot(1,3,3).add_child(display_gt_and_controls(e, "location_df", with_points=True))

In [ ]:
##### ct_midpoint_25 	0.024405 	0.412410 	0.881352 	2 	subway_underground 	train_bus_ebike_mtv_ucb 	mtv_to_berkeley_sf_bart
# subway, trajectory based is bad, nothing to be done
sel_name = "mtv_to_berkeley_sf_bart/subway_underground_2"
e = ref_tree["train_bus_ebike_mtv_ucb"][sel_name]
fig = bre.Figure()
fig.add_subplot(1,3,1).add_child(display_gt_and_reference(e, "travel_forward_25", with_points=True))
fig.add_subplot(1,3,2).add_child(display_gt_and_reference(e, "ct_midpoint_25", with_points=True))
fig.add_subplot(1,3,3).add_child(display_gt_and_controls(e, "location_df", with_points=True))

In [ ]:
##### ct_midpoint_25 	0.118120 	0.337299 	0.997898 	1 	commuter_rail_aboveground 	train_bus_ebike_mtv_ucb 	mtv_to_berkeley_sf_bart
sel_name = "mtv_to_berkeley_sf_bart/commuter_rail_aboveground_1"
e = ref_tree["train_bus_ebike_mtv_ucb"][sel_name]
fig = bre.Figure()
fig.add_subplot(1,3,1).add_child(display_gt_and_reference(e, "travel_forward_25", with_points=True))
fig.add_subplot(1,3,2).add_child(display_gt_and_reference(e, "ct_midpoint_25", with_points=True))
fig.add_subplot(1,3,3).add_child(display_gt_and_controls(e, "location_df", with_points=True))


In [ ]:
##### Considering entry suburb_bicycling suburb_bicycling 0
##### max_gap for tf = 0.03349313290251375 > ct = 0.0008587982795516346 and density 0.7205317565438214 < 0.822728751810466, returning ct len = 958 not tf len = 839

sel_name = "suburb_bicycling/suburb_bicycling_0"
e = ref_tree["unimodal_trip_car_bike_mtv_la"][sel_name]
fig = bre.Figure()
fig.add_subplot(1,3,1).add_child(display_gt_and_reference(e, "travel_forward_25", with_points=True))
fig.add_subplot(1,3,2).add_child(display_gt_and_reference(e, "ct_midpoint_25", with_points=True))
fig.add_subplot(1,3,3).add_child(display_gt_and_controls(e, "location_df", with_points=True))

In [ ]:
def get_centroid(curr_map):
    bbox = []
    [bbox.extend(reversed(p)) for p in curr_map.get_bounds()]
    return shp.geometry.box(*bbox).centroid

In [ ]:
import emeval.metrics.dist_calculations as emd